In [21]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from scipy.optimize import minimize
import matplotlib.pyplot as plt
import firm_revised

In [22]:
seed = 100

In [23]:
df = pd.read_csv(f'/Users/popovici/Desktop/Thesis/markdown_estimation/data/market_{seed}.csv')
print(df)

       price      cost  product  time      Car1      Car2    mshare   profits  \
0   2.282848  1.106668        1     1  5.543405  3.672721  0.013271  0.015609   
1   2.201483  1.025308        2     1  5.278369  2.895589  0.045398  0.053396   
2   2.676177  1.500000        3     1  5.424518  2.468720  0.022874  0.026904   
3   2.176177  1.000000        4     1  5.844776  4.029733  0.019231  0.022619   
4   2.176176  1.000000        5     1  5.004719  2.561864  0.120194  0.141369   
..       ...       ...      ...   ...       ...       ...       ...       ...   
75  2.772708  1.000000       16     4  5.978624  3.055676  0.003180  0.005637   
76  2.772693  1.000000       17     4  5.811683  3.222400  0.015653  0.027748   
77  3.238433  1.465738       18     4  5.171941  1.556783  0.020648  0.036603   
78  3.079565  1.306845       19     4  5.816225  2.243648  0.003834  0.006797   
79  2.772694  1.000000       20     4  5.274074  3.816454  0.053131  0.094185   

     markups  
0   1.062812

In [24]:
# All the parameters of interest 
beta = np.array([2, -0.5, -0.3])
mu = 0.5
omega = 1


# The number of firms in the market
J = 20

# The number of product characteristics 
K = 2

# The number of consumers in the market 
N = 10

# The number of period that I want to run the market for 
T = 5

In [31]:
# Unpacking the X and the price
X1 = np.array(df['Car1'][:J])
X2 = np.array(df['Car2'][:J])
all_X = np.column_stack((X1, X2))
X0 = np.ones(J)
X = np.column_stack((X0, all_X))

eq_price = np.array(df['price'])
print(eq_price.shape)

true_share = np.array(df['mshare'])
print(true_share)

all_est_shares = np.zeros(J*(T-1))
print(all_est_shares)


(80,)
[0.01327118 0.04539763 0.02287416 0.01923073 0.12019415 0.02472359
 0.00609288 0.03847023 0.02609582 0.01484625 0.01769666 0.0285524
 0.02536679 0.06019334 0.26053935 0.02456399 0.0743556  0.09478461
 0.02069011 0.03244506 0.03394447 0.06285473 0.22299702 0.00480897
 0.01029162 0.03761495 0.0128603  0.02955567 0.05100518 0.05973234
 0.04387961 0.04494991 0.01200075 0.0083902  0.02976295 0.04833791
 0.02394256 0.02744951 0.03781295 0.16586162 0.01359769 0.00442846
 0.00997764 0.00233315 0.12221126 0.00591062 0.00312658 0.00400623
 0.00579349 0.00767406 0.00660676 0.05547327 0.00218836 0.00721351
 0.01041433 0.00420129 0.01502564 0.16549867 0.01328514 0.00878235
 0.00963682 0.02695072 0.00920074 0.00326582 0.01119305 0.70735821
 0.00801275 0.00647747 0.00625614 0.00798765 0.00803363 0.00757676
 0.01816162 0.02461472 0.03282678 0.00317962 0.01565309 0.02064822
 0.0038342  0.05313078]
[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0.

In [26]:
# The idea is that you want to min the distance between the true share and the made up share by optimizing the fiven vector theta that determines the share 

def f(theta, true_share, N, J, X, price):
    beta = theta[:K+1]
    mu = theta[K+1]
    omega = theta[K+2]
    # make a numpy array all estimated shares 
    for t in range(0, T-1):
        eq_price_slice = price[t*J:(t+1)*J]
        v_p = np.random.normal(0, 1, size = N)
        e = np.random.gumbel(size=N*J)
        est_share = firm_revised.share(N, J, X, v_p, eq_price_slice, beta, mu, omega, e)
        all_est_shares[t*J:(t+1)*J] = est_share
        print(all_est_shares)

    return np.linalg.norm(true_share - all_est_shares)

In [27]:
theta_0 = np.array([1., 1., 1., 1., 1.])

In [28]:
res = minimize(f, theta_0, args=(true_share, N, J, X, eq_price), method = 'Nelder-Mead')
optim_vec = res.x
print(optim_vec)

[0.01859822 0.00583803 0.00318399 0.19762086 0.00298981 0.00781214
 0.02833444 0.07964489 0.00392214 0.00493108 0.00828908 0.03899643
 0.05013654 0.0428879  0.00427158 0.44547339 0.0097726  0.00334019
 0.00766145 0.03629357 0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.        ]
[0.01859822 0.00583803 0.00318399 0.19762086 0.00298981 0.00781214
 0.02833444 0.07964489 0.00392214 0.00493108 0.00828908 0.03899643
 0.05013654 0.0428879  0.00427158 0.44547339 0.0097

In [29]:
all_val_b1 = []
for l in range(1, 1):
    res = minimize(f, theta_0, args=(true_share, N, J, X, eq_price), method = 'Nelder-Mead')
    optim_vec = res.x
    all_val_b1.append(optim_vec[1])

arr = np.array(all_val_b1)
print(np.mean(arr))


nan


/Users/popovici/Library/Python/3.9/lib/python/site-packages/numpy/core/fromnumeric.py:3432: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/Users/popovici/Library/Python/3.9/lib/python/site-packages/numpy/core/_methods.py:190: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


In [30]:
print(all_val_b1)

[]
